In [2]:
import shutil
import subprocess
import glob
from tqdm import tqdm
import numpy as np
import os
import argparse

import torch
from torch import nn
import torch.nn.functional as F
import pretrainedmodels
from pretrainedmodels import utils

C, H, W = 3, 224, 224


def extract_frames(video, dst):
    with open(os.devnull, "w") as ffmpeg_log:
        if os.path.exists(dst):
            print(" cleanup: " + dst + "/")
            shutil.rmtree(dst)
        os.makedirs(dst)
        video_to_frames_command = ["ffmpeg",
                                   # (optional) overwrite output file if it exists
                                   '-y',
                                   '-i', video,  # input file
                                   '-vf', "scale=400:300",  # input file
                                   '-qscale:v', "2",  # quality for JPEG
                                   '{0}/%06d.jpg'.format(dst)]
        subprocess.call(video_to_frames_command,
                        stdout=ffmpeg_log, stderr=ffmpeg_log)

        
#Sample some frames from video and then convert to rgb and then pass through model to get features 
#and the save them.

def extract_feats(params, model, load_image_fn):
    global C, H, W
    model.eval()

    dir_fc = params['output_dir']
    if not os.path.isdir(dir_fc):
        os.mkdir(dir_fc)
    print("save video feats to %s" % (dir_fc))
    video_list = glob.glob(os.path.join(params['video_path'], '*.mp4'))
    caption_path = 'data/captions/train.json'
    videos_json = json.load(open(path, 'r'))
    for video in tqdm(video_list):
        print("name: ",video)
        video_id = video.split("/")[-1].split(".")[0]
        print("id: ",video_id)
        captions = []
        if video_id in videos_json:
            captions = videos_json[video_id]['sentences']
        else:
            print("Caption not found for ",video_id)
        
        dst = params['model'] + '_' + video_id
        extract_frames(video, dst)

        image_list = sorted(glob.glob(os.path.join(dst, '*.jpg')))
        samples = np.round(np.linspace(
            0, len(image_list) - 1, params['n_frame_steps']))
        image_list = [image_list[int(sample)] for sample in samples]
        images = torch.zeros((len(image_list), C, H, W))
        for iImg in range(len(image_list)):
            img = load_image_fn(image_list[iImg])
            images[iImg] = img
        with torch.no_grad():
            fc_feats = model(images).squeeze()
            #fc_feats = model(images.cuda()).squeeze()
        img_feats = fc_feats.cpu().numpy()
        # Save the inception features
        outfile = os.path.join(dir_fc, video_id + '.npy')
        np.save(outfile, img_feats)
        # cleanup
        shutil.rmtree(dst)


if __name__ == '__main__':
    parser = argparse.ArgumentParser()
    parser.add_argument("--gpu", dest='gpu', type=str, default='0',
                        help='Set CUDA_VISIBLE_DEVICES environment variable, optional')
    parser.add_argument("--output_dir", dest='output_dir', type=str,
                        default='data/feats/resnet152', help='directory to store features')
    parser.add_argument("--n_frame_steps", dest='n_frame_steps', type=int, default=40,
                        help='how many frames to sampler per video')

    parser.add_argument("--video_path", dest='video_path', type=str,
                        default='data/train-video', help='path to video dataset')
    parser.add_argument("--model", dest="model", type=str, default='resnet152',
                        help='the CNN model you want to use to extract_feats')
    
    import sys
    sys.argv=['']
    del sys
    args = parser.parse_args()
    os.environ['CUDA_VISIBLE_DEVICES'] = args.gpu
    params = vars(args)
    if params['model'] == 'inception_v3':
        C, H, W = 3, 299, 299
        model = pretrainedmodels.inceptionv3(pretrained='imagenet')
        load_image_fn = utils.LoadTransformImage(model)

    elif params['model'] == 'resnet152':
        C, H, W = 3, 224, 224
        model = pretrainedmodels.resnet152(pretrained='imagenet')
        load_image_fn = utils.LoadTransformImage(model)

    elif params['model'] == 'inception_v4':
        C, H, W = 3, 299, 299
        model = pretrainedmodels.inceptionv4(
            num_classes=1000, pretrained='imagenet')
        load_image_fn = utils.LoadTransformImage(model)

    else:
        print("doesn't support %s" % (params['model']))

    model.last_linear = utils.Identity()
    #model = nn.DataParallel(model)
    
    #model = model.cuda()
    extract_feats(params, model, load_image_fn)

  0%|          | 0/1 [00:00<?, ?it/s]

save video feats to data/feats/resnet152
name:  data/train-video/v_-AjZCBMb4qU.mp4
id:  v_-AjZCBMb4qU
 cleanup: resnet152_v_-AjZCBMb4qU/


100%|██████████| 1/1 [00:21<00:00, 21.52s/it]


In [3]:
a=np.load('data/feats/resnet152/v_-AjZCBMb4qU.npy')


In [7]:
import re
import json
import argparse
import numpy as np


def build_vocab(vids, params):
    count_thr = params['word_count_threshold']
    # count up the number of words
    counts = {}
    for vid, caps in vids.items():
        for cap in caps['captions']:
            ws = re.sub(r'[.!,;?]', ' ', cap).split()
            for w in ws:
                counts[w] = counts.get(w, 0) + 1
    # cw = sorted([(count, w) for w, count in counts.items()], reverse=True)
    total_words = sum(counts.values())
    bad_words = [w for w, n in counts.items() if n <= count_thr]
    vocab = [w for w, n in counts.items() if n > count_thr]
    bad_count = sum(counts[w] for w in bad_words)
    print('number of bad words: %d/%d = %.2f%%' %
          (len(bad_words), len(counts), len(bad_words) * 100.0 / len(counts)))
    print('number of words in vocab would be %d' % (len(vocab), ))
    print('number of UNKs: %d/%d = %.2f%%' %
          (bad_count, total_words, bad_count * 100.0 / total_words))
    # lets now produce the final annotations
    if bad_count > 0:
        # additional special UNK token we will use below to map infrequent words to
        print('inserting the special UNK token')
        vocab.append('<UNK>')
    for vid, caps in vids.items():
        caps = caps['captions']
        vids[vid]['final_captions'] = []
        for cap in caps:
            ws = re.sub(r'[.!,;?]', ' ', cap).split()
            caption = [
                '<sos>'] + [w if counts.get(w, 0) > count_thr else '<UNK>' for w in ws] + ['<eos>']
            vids[vid]['final_captions'].append(caption)
    return vocab


def main(params):
    videos = json.load(open(params['input_json'], 'r'))['sentences']
    video_caption = {}
    for i in videos:
        if i['video_id'] not in video_caption.keys():
            video_caption[i['video_id']] = {'captions': []}
        video_caption[i['video_id']]['captions'].append(i['caption'])
    # create the vocab
    vocab = build_vocab(video_caption, params)
    itow = {i + 2: w for i, w in enumerate(vocab)}
    wtoi = {w: i + 2 for i, w in enumerate(vocab)}  # inverse table
    wtoi['<eos>'] = 0
    itow[0] = '<eos>'
    wtoi['<sos>'] = 1
    itow[1] = '<sos>'

    out = {}
    out['ix_to_word'] = itow
    out['word_to_ix'] = wtoi
    out['videos'] = {'train': [], 'val': [], 'test': []}
    videos = json.load(open(params['input_json'], 'r'))['videos']
    for i in videos:
        out['videos'][i['split']].append(int(i['id']))
    json.dump(out, open(params['info_json'], 'w'))
    json.dump(video_caption, open(params['caption_json'], 'w'))


if __name__ == "__main__":
    parser = argparse.ArgumentParser()

    # input json
    parser.add_argument('--input_json', type=str, default='data/videodatainfo_2017.json',
                        help='msr_vtt videoinfo json')
    parser.add_argument('--info_json', default='data/info.json',
                        help='info about iw2word and word2ix')
    parser.add_argument('--caption_json', default='data/caption.json', help='caption json file')


    parser.add_argument('--word_count_threshold', default=1, type=int,
                        help='only words that occur more than this number of times will be put in vocab')

    args = parser.parse_args()
    params = vars(args)  # convert to ordinary dict
    main(params)

(40, 2048)

In [ ]:
# import re
# import json
# import argparse
# import numpy as np


# def build_vocab(vids, params):
#     count_thr = params['word_count_threshold']
#     # count up the number of words
#     counts = {}
#     for vid, caps in vids.items():
#         for cap in caps['captions']:
#             ws = re.sub(r'[.!,;?]', ' ', cap).split()
#             for w in ws:
#                 counts[w] = counts.get(w, 0) + 1
#     # cw = sorted([(count, w) for w, count in counts.items()], reverse=True)
#     total_words = sum(counts.values())
#     bad_words = [w for w, n in counts.items() if n <= count_thr]
#     vocab = [w for w, n in counts.items() if n > count_thr]
#     bad_count = sum(counts[w] for w in bad_words)
#     print('number of bad words: %d/%d = %.2f%%' %
#           (len(bad_words), len(counts), len(bad_words) * 100.0 / len(counts)))
#     print('number of words in vocab would be %d' % (len(vocab), ))
#     print('number of UNKs: %d/%d = %.2f%%' %
#           (bad_count, total_words, bad_count * 100.0 / total_words))
#     # lets now produce the final annotations
#     if bad_count > 0:
#         # additional special UNK token we will use below to map infrequent words to
#         print('inserting the special UNK token')
#         vocab.append('<UNK>')
#     for vid, caps in vids.items():
#         caps = caps['captions']
#         vids[vid]['final_captions'] = []
#         for cap in caps:
#             ws = re.sub(r'[.!,;?]', ' ', cap).split()
#             caption = [
#                 '<sos>'] + [w if counts.get(w, 0) > count_thr else '<UNK>' for w in ws] + ['<eos>']
#             vids[vid]['final_captions'].append(caption)
#     return vocab


# def main(params):
#     videos = json.load(open(params['input_json'], 'r'))['sentences']
#     video_caption = {}
#     for i in videos:
#         if i['video_id'] not in video_caption.keys():
#             video_caption[i['video_id']] = {'captions': []}
#         video_caption[i['video_id']]['captions'].append(i['caption'])
#     # create the vocab
#     vocab = build_vocab(video_caption, params)
#     itow = {i + 2: w for i, w in enumerate(vocab)}
#     wtoi = {w: i + 2 for i, w in enumerate(vocab)}  # inverse table
#     wtoi['<eos>'] = 0
#     itow[0] = '<eos>'
#     wtoi['<sos>'] = 1
#     itow[1] = '<sos>'

#     out = {}
#     out['ix_to_word'] = itow
#     out['word_to_ix'] = wtoi
#     out['videos'] = {'train': [], 'val': [], 'test': []}
#     videos = json.load(open(params['input_json'], 'r'))['videos']
#     for i in videos:
#         out['videos'][i['split']].append(int(i['id']))
#     json.dump(out, open(params['info_json'], 'w'))
#     json.dump(video_caption, open(params['caption_json'], 'w'))


# if __name__ == "__main__":
#     parser = argparse.ArgumentParser()

#     # input json
#     parser.add_argument('--input_json', type=str, default='data/activity_net.v1-2.min.json',
#                         help='msr_vtt videoinfo json')
#     parser.add_argument('--info_json', default='data/info.json',
#                         help='info about iw2word and word2ix')
#     parser.add_argument('--caption_json', default='data/captions/train.json', help='caption json file')


#     parser.add_argument('--word_count_threshold', default=1, type=int,
#                         help='only words that occur more than this number of times will be put in vocab')

#     args = parser.parse_args()
#     params = vars(args)  # convert to ordinary dict
#     main(params)

In [2]:
import re
import json
import argparse
import numpy as np


def build_vocab(vids, params):
    count_thr = params['word_count_threshold']
    # count up the number of words
    counts = {}
    for vid, caps in vids.items():
        for cap in caps['captions']:
            print("caption: ",cap)
            ws = re.sub(r'[.!,;?]', ' ', cap).split()
            for w in ws:
                counts[w] = counts.get(w, 0) + 1
    # cw = sorted([(count, w) for w, count in counts.items()], reverse=True)
    total_words = sum(counts.values())
    bad_words = [w for w, n in counts.items() if n <= count_thr]
    vocab = [w for w, n in counts.items() if n > count_thr]
    bad_count = sum(counts[w] for w in bad_words)
    print('number of bad words: %d/%d = %.2f%%' %
          (len(bad_words), len(counts), len(bad_words) * 100.0 / len(counts)))
    print('number of words in vocab would be %d' % (len(vocab), ))
    print('number of UNKs: %d/%d = %.2f%%' %
          (bad_count, total_words, bad_count * 100.0 / total_words))
    # lets now produce the final annotations
    if bad_count > 0:
        # additional special UNK token we will use below to map infrequent words to
        print('inserting the special UNK token')
        vocab.append('<UNK>')
    for vid, caps in vids.items():
        caps = caps['captions']
        vids[vid]['final_captions'] = []
        for cap in caps:
            ws = re.sub(r'[.!,;?]', ' ', cap).split()
            caption = [
                '<sos>'] + [w if counts.get(w, 0) > count_thr else '<UNK>' for w in ws] + ['<eos>']
            vids[vid]['final_captions'].append(caption)
    return vocab


def main(params):
    videos = json.load(open(params['input_json'], 'r'))['database']
    video_caption = {}
    captions = json.load(open('data/captions/train.json', 'r'))
    for i in captions:
        if i not in video_caption.keys():
            video_caption[i] = {'captions': []}    
        video_caption[i]['captions']= captions[i]['sentences']
    # create the vocab
    vocab = build_vocab(video_caption, params)
    itow = {i + 2: w for i, w in enumerate(vocab)}
    wtoi = {w: i + 2 for i, w in enumerate(vocab)}  # inverse table
    wtoi['<eos>'] = 0
    itow[0] = '<eos>'
    wtoi['<sos>'] = 1
    itow[1] = '<sos>'

    out = {}
    out['ix_to_word'] = itow
    out['word_to_ix'] = wtoi
    out['videos'] = {'training': [], 'validation': [], 'testing': []}
    for i in videos:
        out['videos'][videos[i]['subset']].append(i)
    json.dump(out, open(params['info_json'], 'w'))
    json.dump(video_caption, open(params['caption_json'], 'w'))


if __name__ == "__main__":
    parser = argparse.ArgumentParser()

    # input json
    parser.add_argument('--input_json', type=str, default='data/activity_net.v1-2.min.json',
                        help='msr_vtt videoinfo json')
    parser.add_argument('--info_json', default='data/info.json',
                        help='info about iw2word and word2ix')
    parser.add_argument('--caption_json', default='data/captions/out_captions.json', help='caption json file')


    parser.add_argument('--word_count_threshold', default=1, type=int,
                        help='only words that occur more than this number of times will be put in vocab')
    
    import sys
    sys.argv=['']
    del sys
    args = parser.parse_args()
    params = vars(args)  # convert to ordinary dict
    main(params)

caption:  A young woman is seen standing in a room and leads into her dancing.
caption:   The girl dances around the room while the camera captures her movements.
caption:   She continues dancing around the room and ends by laying on the floor.
caption:  The video starts with a title logo sequence.
caption:   A man and woman are in a living room demonstrating exercises.
caption:   The woman lays on the ground.
caption:   The man starts pointing to different areas of the woman's body as she does an exercise.
caption:   The woman begins to do small sit ups.
caption:   The woman ends with a final title logo sequence.
caption:  Two people are seen moving around a kitchen quickly performing various tasks and sitting down.
caption:   They then wax down a ski in the kitchen while continuing to move around.
caption:  We see a hallway with a wooden floor.
caption:   A dog in socks walks slowly out onto the floor as a lady films him.
caption:   The dog turns around and goes back to the other roo

caption:   There are several images of her from behind with very long hair.
caption:   We then see numerous images of her with her hair cut off to shoulder length.
caption:  A man in a red coat is outside on a snowboard.
caption:   He starts going down a course and doing some really cool tricks while moving.
caption:   Some men are rubbing down their boards and another gets on the field and starts doing some flips and stuff in mid air.
caption:   These are all pretty experienced people on the boards, they are even boarding through water and having a good time.
caption:  woman is standing talking to the camera holding a microphone and interviewing voleyball players.
caption:   men are standing in a sandy field being interviewed.
caption:   men are in sandy field showing he girl how to play beach soccer.
caption:   woman is sin front of the net talking to the camera.
caption:  A man gets pumped up to do a long jump then does it.
caption:    Others go next and try to get the crowd pumped 

caption:    One of the boys puts on a football helmet and stands on the side lines catching the ball.
caption:  On a track, a runner gets ready to perform.
caption:   He runs and skips along the way, jumping high at the end.
caption:   He walks along the track after being finished.
caption:   The man runs and jumps again.
caption:   The runner talks to someone.
caption:  Three men wearing snowboards get out a ski lift, and a man tie his shoe.
caption:   Then, the men ski down a hill covered with snow.
caption:   A man bend his legs on the snow, then continue skiing with other men.
caption:  A man plays the bagpipes on stage while wearing a Scottish skirt.
caption:   Then, the man ends playing and holds the bagpipes on his left arm.
caption:  A woman is on her hands and knees cutting grass with some scissors.
caption:   The camera pans out to give a full view of her cutting the grass.
caption:   She makes a joke about the grass having split ends and bad roots.
caption:   The camera goes

caption:   Two guys sit on their dirt bike and discuss.
caption:   One guy uses his rear tire to cause dirt to spray.
caption:   The credits of the video are shown.
caption:  A black book called Windmills is on the screen.
caption:    The camera zooms into a dancer.
caption:    VincaniTV comes up on the screen.
caption:    the instructor is talking.
caption:    The instructor is sitting on the floor introducing the move.
caption:    A shot of the move is shown, then the instructor shows how to do it.
caption:    He pushes  himself up on his hand and does another move.
caption:    He is on one knee to show another move.
caption:   The screen goes to another shot of the same move but faster this time.
caption:    The instructor is standing and talking.
caption:    The screen ends with a VincaniTV promo.
caption:  A woman is standing in a camp site.
caption:   She lights matches and throws them into a pile of wood.
caption:  A large group of people are seen playing a game of volley ball w

caption:  Two girls practice fencing in a school gym with protective gear on and a coach against the wall watching and coaching them as they fence.
caption:    The two girls talk to the coach and then begin to fence with each other as the coach motions to where they should stand and navigate the space during the spar.
caption:    Both girls end the spar and remove their head gear as they talk to the coach.
caption:  A woman in a green sweater puts on a face mask.
caption:   She paints a wooden fence.
caption:   She puts news paper onto the fence.
caption:   She pours a bucket of paint into a sprayer.
caption:   She starts spraying the fence with a hose.
caption:  Two men are talking in front of a helicopter.
caption:   A man on a wake board is being pulled by a helicopter in and out of the water.
caption:   He drops from the rope and pulls a parachute and lands on the ground.
caption:  A man is seated on a bench in a park.
caption:   He is playing an old accordian.
caption:   He pushes

...

caption:   Close ups of her feet are shown as well as several other angles of her running.
caption:  A woman with very long hair is standing on a balcony showing off the length of her hair.
caption:   She turns around and faces the camera continuing to brush her hair and display its length.
caption:   She begins to twirl and sway her hair with her back to the camera and that is when the video ends.
caption:  A person is seen unscrewing a bottle of mouth wash and pouring it into a cup.
caption:   The girl then drinks from it and swishes it around her mouth.
caption:   She spits out the mixture and shows off pictures in the end.
caption:  A compilation of shot put is put together, you see many different men getting prepared.
caption:   They turn their bodies very quickly building up as much speed as they can before taking their shot.
caption:   They practice and they do it professionally, it a serious sport that people really enjoy yo be a part of.
caption:   They tend to get very excite

caption:   Finally the driveway is cleared of the leaves.
caption:  We see an opening title screen.
caption:   We see a man in an orange shirt twirl and spin to throw the hammer over 80km .
caption:   Next we see a man in a blue shirt throw 73km.
caption:   We see a man in a white shirt throw 75km.
caption:   The man in orange goes again and throws 81km.
caption:  A man sits on top of a camel.
caption:   The camel stands up and a man in front leads it.
caption:   A red barn is seen behind them.
caption:   The camel sits back down and the man gets off.
caption:  A woman is seen standing in front of buckets and speaking to the camera.
caption:   She pours water into a bucket while dragging it over as well as mixing cleaning into it and beginning to dump clothes.
caption:   The woman dips the clothes into the bucket and shows where she hangs them and waving to the camera.
caption:  A man carefully washes the side of a car with a sponge.
caption:   The man stands up and washes the windshie

caption:   The man reaches the house and turns to finish the other side of the walkway.
caption:   We see a person spraying an item on their sidewalk.
caption:   We then see two closing screens.
caption:  Two men are in an inside court.
caption:   They play a game of racquetball together.
caption:   They take turns hitting the ball back and forth against the wall.
caption:  A woman is seen putting her hair up in a pony tail with a man watching her on the side.
caption:   She then plays the piano while smiling  and the man continuing to watch her.
caption:  People are paddling in kayaks in a body of water.
caption:   A man takes off in a green kayak.
caption:   A man in a red jacket is talking to the camera.
caption:  A woman and a dog are playing on the grass with a frisbee.
caption:   The dog has the frisbee in its mouth.
caption:   The woman and the dog are playing with a rope.
caption:  At the beach, a group of soccer balls lie next to a man who is kicking them at the goal, protecte

caption:   The first woman pulls items out of a cabinet and places them on the floor.
caption:   A fourth individual is briefly shown in the doorway.
caption:  Two people are on a white slab and they begin fencing one another.
caption:  There are constant stops and the boy closest to the camera keeps winning.
caption:  Both of them keep being reset but the outcome is no different and the lady on the side keeps walking back and forth clicking a black button.
caption:  A man is shown speaking to the camera and leads into a woman trimming the fur on a dog.
caption:   The speaks more to the camera while other dogs are shown groomed and one woman walks away holding two excited dogs.
caption:   More shots of dogs held are shown while the man speaks and the camera pans around the building.
caption:  A logo shows that this video is presented by Expert Village.
caption:   A man in a small blue boat discusses the topic of hand surfing in a hole and gives hints on how to perform this activity.
ca

caption:   He is holding a large steel ball.
caption:   He spins and throws the ball, then walks around the track waiting for his next turn.
caption:  Several outside views of a casino are shown.
caption:   Card players and the dealer at a table are shown engaging in a game inside the casino.
caption:   The dealer deals cards to each player.
caption:   The dealer reveals the dealer's hand.
caption:   One man talks to the camera while another man stands nearby.
caption:  There's a little boy sitting on a bed in the bedroom.
caption:   There is a laundry basket and a lot of clothes on the bed.
caption:   The mother of the boy who is filming the video shows a vacuum cleaner.
caption:   Then she turns the vacuum cleaner on and begins vacuuming the bedroom floor.
caption:   The boy watches his mom vacuum as he jumps on the bed.
caption:   the boy then lays down on the bed as he sees his mother finish the job.
caption:   Then the boy gets off the bed and jumps down to the ground to look unde

In [34]:
import re
import json
import argparse
import numpy as np
path = 'data/captions/train.json'
videos_json = json.load(open(path, 'r'))
#videos_json.keys()
# type(videos_json['v_-AjZCBMb4qU']['sentences'])
for i,j in videos_json.items():
    print(i, j)
    #print(videos_json['v_-AjZCBMb4qU'])


# videos_json['v_-AjZCBMb4qU']['timestamps'][0]

v_QOlSCBRmfWY {'duration': 82.73, 'timestamps': [[0.83, 19.86], [17.37, 60.81], [56.26, 79.42]], 'sentences': ['A young woman is seen standing in a room and leads into her dancing.', ' The girl dances around the room while the camera captures her movements.', ' She continues dancing around the room and ends by laying on the floor.']}
v_ehGHCYKzyZ8 {'duration': 61.72, 'timestamps': [[0, 2.78], [3.09, 61.72], [15.43, 55.24], [17.59, 54], [39.81, 54.62], [56.47, 61.72]], 'sentences': ['The video starts with a title logo sequence.', ' A man and woman are in a living room demonstrating exercises.', ' The woman lays on the ground.', " The man starts pointing to different areas of the woman's body as she does an exercise.", ' The woman begins to do small sit ups.', ' The woman ends with a final title logo sequence.']}
v_nwznKOuZM7w {'duration': 31.65, 'timestamps': [[0, 15.51], [11.39, 31.65]], 'sentences': ['Two people are seen moving around a kitchen quickly performing various tasks and sit

v_xKDHIyd_tWA {'duration': 111.02000000000001, 'timestamps': [[0, 5], [5, 86.04], [5, 85.48], [60.5, 64.94], [86.59, 111.02]], 'sentences': ['The video begins with a title slide.', ' A woman and child are in a park with a jump rope.', ' The woman begins to demonstrate how to use the jump rope while the child attempts to copy her.', ' At one point, another woman in the background runs across the screen while jump roping.', 'The video ends with both women speaking to the camera and a final title sequence.']}
v_-v9YLmGCYO0 {'duration': 72.26, 'timestamps': [[0, 72.26], [0, 45.89], [45.16, 72.26]], 'sentences': ['A baby is sitting in a swing.', ' The baby is laughing and shaking its feet.', ' The baby turns to the side of the swing.']}
v_5kBKAfEX7XA {'duration': 45.65, 'timestamps': [[0, 25.79], [13.47, 43.6]], 'sentences': ['An athlete is seen walking up to a set of uneven bars and begins performing a gymnastics routine on the bars.', ' He continues moving around on the bars and ends by j

v_81F42Yyw_iY {'duration': 66.67, 'timestamps': [[11, 55], [51.33, 58.67], [59, 66.67]], 'sentences': ['A woman pole vaults over a tall bar.', ' She lands on a yellow mat under her.', ' Words come onto the screen at the end.']}
v_LZleSe6Kovg {'duration': 27.75, 'timestamps': [[0, 27.75], [3.47, 24.42], [24.7, 27.75]], 'sentences': ['A man is wearing a white robe with a black belt.', ' He starts doing karate moves in a room.', ' He stands up right at the end.']}
v_3cjtV-ldvto {'duration': 212.14, 'timestamps': [[0, 16.97], [16.97, 43.49], [43.49, 59.4], [59.4, 149.56], [149.56, 169.71], [170.77, 212.14]], 'sentences': ['woman put an egg on a bowl and mix it with vanilla.', ' quick oats and baking powder, cocoa powder and salt are mixed in a bowl.', ' a chocolate bar are cut in pieces with nuts and put in a bowl.', ' sugar and butter are mixed in a bowl till cream and put the vanilla and the powder ingredients with the chocolate and he nuts.', ' themix is wrap and put in a refrigerator.'

v_XqxJsWQqKRk {'duration': 173.29, 'timestamps': [[0, 14.73], [14.73, 23.39], [25.13, 33.79], [33.79, 55.45], [52.85, 57.19], [57.19, 64.98], [64.98, 71.92], [71.92, 122.17], [122.17, 123.04], [123.04, 135.17], [135.17, 173.29]], 'sentences': ['A white screen with blue and white shapes and black words flash across the screen.', " A smiling black man is in a residential kitchen and he's wearing a santa hat and pouring ingredients into a large bowl.", ' A hand pushes a clear bowl filled with dark figs and a cutting board appears immediately afterwards and the instructions on the screen say to cut the stems off of 1lb of figs and quarter them.', ' While the list of ingredients are shown that include: 1lb Figs, 1lb Raisins, 1lb Cherries, 1lb Currants, 1lb Prunes, Port Wine and Angostura Bitters; they are all poured into a white bucket.', ' Stirring begins immediately and the instructions on the screen say to let it soak for at least two weeks to up to 30 days.', ' 30 days later the content

v_zp86ztwZEKk {'duration': 88.42, 'timestamps': [[0, 13.26], [13.26, 19.45], [13.26, 88.42]], 'sentences': ['A talking man dressed in athletic gear is standing on a very green field and the words on the bottom left say his name is Neil Macmillan and his title is Head Coach.', 'A large group of girls dressed in athletic gear are shown playing land hockey, and the people not playing are dressed for cold weather.', ' Clips of the man continue to play and rotate from showing the man and the girls playing land hockey until they are done playing.']}
v_cNCkHqOnJV0 {'duration': 234.26, 'timestamps': [[0, 78.48], [49.19, 179.21], [122.98, 223.71]], 'sentences': ['The sky is shown that leads into a man speaking to the camera with his friend.', ' Several people are then seen sitting in tubes riding down a river past one another.', ' The people continuing riding down the river through tunnels and paths while the man still speaks to the camera.']}
v_FwV1XbjLJHY {'duration': 113.36, 'timestamps': [[

v_DDZFQKi1v2U {'duration': 112.34, 'timestamps': [[0, 28.08], [30.89, 82.57], [79.2, 108.97]], 'sentences': ['A woman is seen laying on the couch with another girl sitting above her.', ' The girl is then shown piercing the nipple of the girl laying down.', ' She finishes the piercing and ends by smiling to the camera.']}
v_FXN6qiDsClw {'duration': 87.38, 'timestamps': [[0, 20.1], [20.1, 31.02], [31.46, 44.13], [44.13, 74.27], [74.27, 80.39], [79.95, 87.38]], 'sentences': ['An animation demonstrating the arc length of a welding type tool emitting heat.', ' A demonstration of the tool emitting heat in real time.', ' A graph illustrating the Long Arc of the tool documenting Voltage and Amperage.', ' The tool is shown in real time emitting heat with a photo of a welded material.', ' A graph illustrates Short Arc with the Voltage and Amperage documented.', ' A man in a blue coat and orange gloves uses the arc tool.']}
v_hS4L3PMfYqA {'duration': 111.32, 'timestamps': [[11.13, 17.81], [17.81,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [40]:
path = 'data/activity_net.v1-2.min.json'
videos = json.load(open(path, 'r'))
videos['database']

{'---9CpRcKoU': {'annotations': [{'label': 'Drinking beer',
    'segment': [0.01, 12.64441]}],
  'duration': 14.07,
  'resolution': '320x240',
  'subset': 'training',
  'url': 'https://www.youtube.com/watch?v=---9CpRcKoU'},
 '--0edUL8zmA': {'annotations': [{'label': 'Dodgeball',
    'segment': [5.46484, 86.71838]}],
  'duration': 92.18,
  'resolution': '640x480',
  'subset': 'training',
  'url': 'https://www.youtube.com/watch?v=--0edUL8zmA'},
 '--1DO2V4K74': {'annotations': [{'label': 'Rock climbing',
    'segment': [30.02588, 205.23186]}],
  'duration': 211.53,
  'resolution': '640x480',
  'subset': 'validation',
  'url': 'https://www.youtube.com/watch?v=--1DO2V4K74'},
 '--6bJUbfpnQ': {'annotations': [{'label': 'Drinking beer',
    'segment': [2.57876, 24.9141]}],
  'duration': 26.75,
  'resolution': '640x480',
  'subset': 'validation',
  'url': 'https://www.youtube.com/watch?v=--6bJUbfpnQ'},
 '-0r0HEwAYiQ': {'annotations': [{'label': 'Vacuuming floor',
    'segment': [27.52112, 39.94